In [1]:
import pandas as pd
from IPython.display import clear_output, Markdown, Math
import ipywidgets as widgets
import os
import glob
import json
import numpy as np
import itertools
import sklearn.utils as sku
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer, HashingVectorizer
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MultiLabelBinarizer

In [2]:
SINGLE_LABEL = True

# simple twitter approach
*for learning emoji usage by single (in the meaning of unconnected) twitter messages*

## loading train data

In [3]:
data_root_folder = "./data_en/" # i created a symlink here

* get all json files in `data_root_folder`

In [4]:
json_files = sorted(glob.glob(data_root_folder + "/*.json"))

----

* so far, only load the first file

In [5]:
twitter_data = pd.read_json(json_files[0], encoding="utf-8")
twitter_data

EMOJI  \
0                           [🔥, 👏]   
1                              [🤦]   
2                              [😄]   
3                              [📷]   
4                           [😩, 😩]   
5                           [😭, 💓]   
6                              [😂]   
7                              [💯]   
8                              [🙄]   
9                        [😟, 😥, 😢]   
10                             [🌻]   
11                       [🍁, 🌺, 🍂]   
12                             [🍃]   
13                          [💭, 🤦]   
14                          [😍, 😘]   
15                             [😜]   
16                          [😂, 🔥]   
17                             [💕]   
18                             [😉]   
19                             [👅]   
20                          [👌, 🙂]   
21                          [🤗, 📺]   
22                             [💯]   
23                       [👅, 💦, 🍑]   
24                             [💔]   
25                       [🤐, 🤐, 🤐]   
26                             [😴]   
27                             [😂]   
28                          [😂, 🙄]   
29              [🎉, 🎂, 🎈, 🎊, 🎁, 💜]   
...                            ...   
68703                          [😕]   
68704                       [😂, 😩]   
68705                          [😂]   
68706                          [💖]   
68707                 [🌆, 👉, 🚖, 📞]   
68708                          [😁]   
68709                          [😋]   
68710                    [👌, 🎃, 😘]   
68711                          [👍]   
68712                          [😭]   
68713                          [😂]   
68714                    [😭, 😭, 💘]   
68715                       [😫, ✋]   
68716                       [😂, 🙁]   
68717                          [😭]   
68718                       [😢, 💔]   
68719                          [🙃]   
68720              [😂, 😂, 😂, 😂, 😂]   
68721                    [👌, 👊, 🙌]   
68722                          [😴]   
68723                 [😂, 😂, 😂, 😂]   
68724                          [😀]   
68725                          [😎]   
68726                          [✨]   
68727                          [🤷]   
68728                          [😘]   
68729                          [😂]   
68730                          [🙏]   
68731                          [💁]   
68732  [🍃, 🌻, 🌻, 🍃, 🍃, 💐, 💐, 🍃, 🙋]   

                                              HASHTAGS  \
0                                                   []   
1                                                   []   
2                                                   []   
3                                                   []   
4                                                   []   
5                                                   []   
6                                                   []   
7                                                   []   
8                                                   []   
9                                                   []   
10                                                  []   
11                                                  []   
12         [#mortdale, #partofthefamily, #gorgeousboy]   
13                                                  []   
14                                     [#7YearsOfKMH2]   
15                                                  []   
16                                                  []   
17                                                  []   
18                                                  []   
19                                 [#footfetishnation]   
20                                                  []   
21                                                  []   
22                                                  []   
23                                                  []   
24                                                  []   
25                                                  []   
26                                                  []   
27                                              

* extracting emojis and text

In [6]:
emojis = twitter_data['EMOJI']
plain_text = twitter_data['text']

* make our plain text more "plain":
    * removing the keyword `<EMOJI>` (just for the beginning)
    * removing remaining useless emojis, like skin modifier etc.

In [7]:
# defining blacklist for modifier emojis:
emoji_blacklist = set([
    chr(0x1F3FB),
    chr(0x1F3FC),
    chr(0x1F3FD),
    chr(0x1F3FE),
    chr(0x1F3FF),
    chr(0x2642),
    chr(0x2640)
])

In [8]:
# filtering them and the EMOJI keyword out:
plain_text = plain_text.str.replace("<EMOJI>","").str.replace("[" + "".join(list(emoji_blacklist)) + "]","")

* trying a multi label vectorizer

In [9]:
def latest(lst):
    return lst[-1] if len(lst) > 0 else 'X' 
def most_common(lst):
    # trying to find the most common used emoji in the given lst
    return max(set(lst), key=lst.count) if len(lst) > 0 else "X" # setting label to 'X' if there is an empty emoji list

In [12]:
mlb_multi = MultiLabelBinarizer()
mlb_single = MultiLabelBinarizer()

multi_labels = mlb_multi.fit_transform(emojis)
single_labels = mlb_single.fit_transform(np.array([latest(x) for x in emojis]))

mlb = mlb_single if SINGLE_LABEL else mlb_multi
labels = single_labels if SINGLE_LABEL else multi_labels

* generate weights:

In [18]:
# at first count over our table
emoji_count = {}


for e_list in emojis:
    for e in set(e_list):
        if e not in emoji_count:
            emoji_count[e] = 0
        emoji_count[e] += 1

emoji_count
emoji_sum = sum([emoji_count[e] for e in emoji_count])

emoji_weights = {}
for e in emoji_count:
    # tfidf for emojis
    emoji_weights[e] = np.log((emoji_sum / emoji_count[e]))

weights_sum= sum([emoji_weights[x] for x in emoji_weights])
    
# normalize:
for e in emoji_weights:
    emoji_weights[e] = emoji_weights[e] / weights_sum

emoji_weights['X'] = 0  # dummy values
emoji_count['X'] = 0

* generating train and test set:

In [15]:
X1, Xt1, y1, yt1 = train_test_split(plain_text, labels, test_size=0.1, random_state=4222)

In [19]:
y1_weights = np.array([(sum([emoji_weights[e] for e in e_list]) / len(e_list)) if len(e_list) > 0 else 0 for e_list in mlb.inverse_transform(y1)])

In [20]:
vectorizer = TfidfVectorizer(stop_words='english')
vec_train = vectorizer.fit_transform(X1)
vec_test = vectorizer.transform(Xt1)

* train. this can take a very long time...

In [21]:
from sklearn.neural_network import MLPClassifier as MLP
from sklearn.multiclass import OneVsRestClassifier as OVRC
from sklearn.tree import DecisionTreeClassifier as DTC

from keras.models import Sequential
from keras.layers import Dense

/home/jonas/.local/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


In [24]:
def train(max_size = 10000, layers=[(1024, 'relu'),(y1[0].shape[0],'softmax')], random_state=4222, ovrc=False, n_iter=5):
    
    model = Sequential()
    
    # build mlp layers:
    keras_layers = []
    first_layer = True
    for layer in layers:
        if first_layer:
            model.add(Dense(units=layer[0], activation=layer[1], input_dim=vectorizer.transform([" "])[0]._shape[1]))
            first_layer = False
        else:
            model.add(Dense(units=layer[0], activation=layer[1]))
    
    #mlp = MLPClassifier(layers=sknn_layers, random_state=random_state, verbose=True, n_iter=n_iter, batch_size=100)
    
    model.compile(loss='categorical_crossentropy',
              optimizer='sgd',
              metrics=['accuracy'])
    
    clf = OVRC(model) if ovrc else model

    clf.fit(vec_train[:max_size].A, y1[:max_size], validation_split=0.2, sample_weight=y1_weights[:max_size])
    
    return clf

In [25]:
clf = train(max_size=10000,layers=[(1200, 'relu'),(1200,'relu'),(y1[0].shape[0],'softmax')])

Train on 8000 samples, validate on 2000 samples
Epoch 1/1
8000/8000 [==============================] - 109s 14ms/step - loss: 0.0042 - acc: 0.0012 - val_loss: 0.0042 - val_acc: 0.0020


In [26]:
X1

62691    <USER> I just finished mine I was extremely ne...
9959     <USER> <USER> <USER> Kinda Gross but yup it's ...
39726    Treating myself to a manicure because even une...
20883    Sarfraz Done it.Congrats.Pakistan Rules the Wo...
2705     I turn 20 in Just over a month and I’ve never ...
20766       <USER> The coolest &amp; beautiful duo ever ❤❤
13242    <USER> Studying abroad in Italy for 3 weeks  i...
32951     You're nice to meeeeee thanks I appreciate that 
7297            <USER> hahahha it kinda does look like me 
10913    <HASHTAG> Ya Rasulullah.,You are the Messenger...
58664                                        <USER> crying
28113    Man my Dad crazy but I miss his Bok Choi soup ...
20698                     <USER> <USER> <USER> Well done!!
45787                                              Mi mess
36076                <USER> schooling all the <HASHTAG>   
66970               <USER> Awww but I’m sure your man can 
34787    TWEET using the hashtag...<HASHTAG> is the rel.

* make a prediction and store it in a csv file:

In [27]:
pred = clf.predict(vectorizer.transform(Xt1))

In [28]:
pred

array([[0.00124256, 0.00124216, 0.00123592, ..., 0.00123677, 0.00123611,
        0.00123534],
       [0.00124442, 0.00123547, 0.00123502, ..., 0.00123892, 0.00123958,
        0.00123556],
       [0.00124413, 0.00123538, 0.00124574, ..., 0.00123829, 0.00123556,
        0.00123374],
       ...,
       [0.00123915, 0.00123915, 0.00123916, ..., 0.00123915, 0.00123916,
        0.00123915],
       [0.00124084, 0.00124438, 0.00123832, ..., 0.00123602, 0.00125055,
        0.00123963],
       [0.00124321, 0.0012361 , 0.00123488, ..., 0.00123589, 0.00124259,
        0.00123691]], dtype=float32)

In [29]:
binary_pred = np.zeros_like(pred)
binary_pred[np.arange(len(pred)), pred.argmax(1)] = 1    

In [30]:
binary_pred[[0,1,2]]

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)

In [31]:
# build a dataframe to visualize test results:
testlist = pd.DataFrame({'text': Xt1, 'teacher': (mlb_single if SINGLE_LABEL else mlb).inverse_transform(yt1), 'predict': (mlb_single if SINGLE_LABEL else mlb).inverse_transform(binary_pred)})

In [32]:
display(testlist)


predict teacher                                               text
15278    (🌠,)    (😅,)                           <USER> <USER> 2 years? ✌
36882    (🕔,)    (😂,)                   tell me why this is me everyday 
65543    (🌍,)    (📌,)  please follow us ::Twitter  ▶️ ▶️  ▶️MARSHMALL...
65893    (😂,)    (🔝,)                                             This  
55496    (🎳,)    (😍,)                                 <USER> Im in love 
61997    (🌍,)    (🌸,)           <USER> Miss you gemmthankyou sooo much❤❤
15819    (🔹,)    (😂,)                                   Me as a parent  
21340    (🌑,)    (😂,)  Really betting my manager rn for tonight’s game  
26691    (🎳,)    (😩,)              Y ES IM A BAD BOY SO I LIKE BAD GIRL 
57025    (🌷,)    (😃,)  <USER> Just downloaded to my fire stick  over ...
17967    (🐔,)    (😍,)           <USER> Love this ! Hollywood is the man 
68555    (🌑,)    (😉,)  <USER> Absolutely but if it had been a banana ...
20784    (💁,)    (🐻,)  La Grasaaaaaaaaa  Reverse Shatter Back Board S...
68300    (🥣,)    (😍,)               I go to New York next month ahhhhhh 
4659     (💍,)    (😭,)  <USER> I’m trying to enjoy it as much as the f...
66706    (🌕,)    (📞,)  : Salamander Resort  <HASHTAG> 🍽️  For Taxi 70...
47510    (🎄,)    (👉,)  For your actions there WILL be consequences. Y...
55294    (😾,)    (😂,)                  <USER> Omg my cousin charging 40 
621      (🌍,)    (🤦,)  Zoey daycare lets her do whatever she want, I ...
31011    (😌,)    (😀,)                                         yeah!  ✌️ 
30659    (🐎,)    (💪,)  This was so much I mean SO MUCH over due for t...
66284    (🤔,)    (🙂,)  Parent contact booking is now open! Please fol...
66758    (🎄,)    (😥,)  <USER> OCONUS we don’t have the Turkey Day buf...
13456    (🌠,)    (💕,)  Dems realtor business partners have lots of ni...
15057    (🥣,)    (😂,)                Ready for the dodgers fans excuses 
188      (🎄,)    (🎉,)                       <USER> Happy Birthday Angge 
5054     (🎄,)    (😂,)                             <USER> <USER> Lawsuit 
18099    (👃,)    (😤,)                     Finna roll this up no excuses 
17120    (🌍,)    (⚡,)       But it’s forever fuck em and keep it gutta ️
14552    (📖,)    (😍,)           I just need to hubby a hockey player up 
...       ...     ...                                                ...
21819    (🎄,)    (😂,)                                   Niggas funny af 
18460    (♿,)    (💁,)  1. Don’t EVER disrespect Thanksgiving cuz yo f...
60291    (🚮,)    (💘,)                            happy bday lexi  <USER>
22623    (🔖,)    (😩,)  Mr.Lazaro said “there’s my girls” when he seen...
87       (🌍,)    (🎈,)  Happy Birthday Blake!!!! I hope you have an am...
2884     (🏄,)    (😉,)  <USER> This would be a good time to do a Week ...
30212    (🧘,)    (📌,)                         <USER> Done, pls ❤️  y FAV
55813    (😾,)    (😍,)    There is just something about <USER>  <HASHTAG>
11657    (💚,)    (😴,)                             <USER> you're  brudda!
18215    (🐹,)    (🤷,)                            Not being depressed ‍️ 
48609    (🧘,)    (🤑,)  <USER> I ❤ you. My woman crush everyday as alw...
16079    (🥣,)    (⚓,)  I added a video to a <USER> playlist  🛳 ️ The ...
28380    (🥣,)    (😂,)                                           Dodgers 
41212    (🌍,)    (🔴,)                                  [LIVE] on <USER> 
67555    (🔗,)    (💞,)  • <USER> my precious Niya always checking up o...
45490    (🕔,)    (🤷,)  If you wanna make things right it go both ways ‍️
54052    (🌍,)    (😢,)                                     Poor baby!!!  
54517    (🐹,)    (😚,)    <USER> happy birthday, hope you have a good day
24047    (🌷,)    (😌,)  Don’t get mad when them haters stare let em lo...
253      (🥄,)    (😎,)  Sag season right around the corner. 25 on the ...
64707    (🎸,)    (😇,)                      <USER> Let’s see his costume 
34279    (🌯,)    (😥,)                              <USER> I AM NERVOUS!!
58342    (🤝,)    (🙌,)                         <USER> This looks 

In [33]:
testlist.to_csv('test.csv')

* a simple output widget for testing:

In [36]:
out = widgets.Output()

t = widgets.Text()
b = widgets.Button(
    description='get smiley',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Click me',
    icon='check'
)



def handle_submit(sender):
    with out:
        clear_output()
    with out:
        pred = clf.predict(vectorizer.transform([t.value]))
        
        #binary_pred = np.zeros_like(pred)
        #binary_pred[np.arange(len(pred)), pred.argmax(1)] = 1
        
        binary_pred = []
        
        s = np.argsort(pred[0])[-5:]
        
        for i in s:
            b = np.zeros_like(pred[0])
            b[i] = 1
            binary_pred.append(b)
        
        binary_pred = np.array(binary_pred)
        
        display(Markdown("# " + str((mlb_single if SINGLE_LABEL else mlb).inverse_transform(binary_pred))))

b.on_click(handle_submit)
    
display(t)
display(widgets.VBox([b, out]))  

Text(value='')

VBox(children=(Button(description='get smiley', icon='check', style=ButtonStyle(), tooltip='Click me'), Output()))

In [44]:
import numpy as np

y_trans = mlb.inverse_transform(yt1)
pred_trans = mlb.inverse_transform(yt1)

# evaluate accuracy
pos = 0
neg = 0
all = 0
for entry in range(len(y_trans)):
    if len(np.intersect1d(y_trans[entry], pred_trans[entry])) > 0:
        pos += 1
    else:
        neg += 1
    all += 1
print(pos/all)
print(neg)

0.9991493705341953
15
